In [ ]:
# 读取配置
from config_jingbo import *
# from config_tansuanli import *
# from config_juxiting import *
from lib.dataread import *
from lib.tools import *
from models.nerulforcastmodels import ex_Model,model_losss,brent_export_pdf,tansuanli_export_pdf,pp_export_pdf

import glob
import torch
torch.set_float32_matmul_precision("high")

sqlitedb = SQLiteHandler(db_name) 
sqlitedb.connect()


signature = BinanceAPI(APPID, SECRET)
etadata = EtaReader(signature=signature,
                        classifylisturl = classifylisturl,
                        classifyidlisturl=classifyidlisturl,
                        edbcodedataurl=edbcodedataurl,
                        edbcodelist=edbcodelist,
                        edbdatapushurl=edbdatapushurl,
                        edbdeleteurl=edbdeleteurl,
                        edbbusinessurl=edbbusinessurl
                        )
# 获取数据
if is_eta:
    # eta数据
    logger.info('从eta获取数据...')
    signature = BinanceAPI(APPID, SECRET)
    etadata = EtaReader(signature=signature,
                                classifylisturl = classifylisturl,
                                classifyidlisturl=classifyidlisturl,
                                edbcodedataurl=edbcodedataurl,
                                edbcodelist=edbcodelist,
                                edbdatapushurl=edbdatapushurl,
                                edbdeleteurl=edbdeleteurl,
                                edbbusinessurl=edbbusinessurl,
                                )

    df_zhibiaoshuju,df_zhibiaoliebiao = etadata.get_eta_api_yuanyou_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理
    # df_zhibiaoshuju,df_zhibiaoliebiao =  etadata.get_eta_api_pp_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理

    
    # 数据处理
    df = datachuli(df_zhibiaoshuju,df_zhibiaoliebiao,y = y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time) 

else:
    logger.info('读取本地数据：'+os.path.join(dataset,data_set))
    df = getdata(filename=os.path.join(dataset,data_set),y=y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time)  # 原始数据，未处理

# 更改预测列名称
df.rename(columns={y:'y'},inplace=True)
    
if is_edbnamelist:
    df = df[edbnamelist]     
df.to_csv(os.path.join(dataset,'指标数据.csv'), index=False)
# 保存最新日期的y值到数据库
# 取第一行数据存储到数据库中
first_row = df[['ds','y']].tail(1)
# 将最新真实值保存到数据库
if not sqlitedb.check_table_exists('trueandpredict'):
    first_row.to_sql('trueandpredict',sqlitedb.connection,index=False)
else:
    for row in first_row.itertuples(index=False):
        row_dict = row._asdict()
        check_query = sqlitedb.select_data('trueandpredict',where_condition = f"ds = '{row.ds}'")
        if len(check_query) > 0:
            set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
            sqlitedb.update_data('trueandpredict',set_clause,where_condition = f"ds = '{row.ds}'")
            continue
        sqlitedb.insert_data('trueandpredict',tuple(row_dict.values()),columns=row_dict.keys())

import datetime
# 判断当前日期是不是周一
is_weekday = datetime.datetime.now().weekday() == 3
if is_weekday:
    logger.info('今天是周一，更新预测模型')
    # 计算最近20天预测残差最低的模型名称

    model_results = sqlitedb.select_data('trueandpredict',order_by = "ds DESC",limit = "20")
    model_results = model_results.dropna()
    modelnames  = model_results.columns.to_list()[2:] 
    for col in model_results[modelnames].select_dtypes(include=['object']).columns:
        model_results[col] = model_results[col].astype(np.float32)
    # 计算每个预测值与真实值之间的偏差率
    for model in modelnames:
        model_results[f'{model}_abs_error_rate'] = abs(model_results['y'] - model_results[model]) / model_results['y']

    # 获取每行对应的最小偏差率值
    min_abs_error_rate_values = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].min(), axis=1)
    # 获取每行对应的最小偏差率值对应的列名
    min_abs_error_rate_column_name = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].idxmin(), axis=1)
    # 将列名索引转换为列名
    min_abs_error_rate_column_name = min_abs_error_rate_column_name.map(lambda x: x.split('_')[0])
    # 取出现次数最多的模型名称
    most_common_model = min_abs_error_rate_column_name.value_counts().idxmax()
    logger.info(f"最近20天预测残差最低的模型名称：{most_common_model}")

    # 保存结果到数据库
    
    if not sqlitedb.check_table_exists('most_model'):
        sqlitedb.create_table('most_model',columns="ds datetime, most_common_model TEXT")
    sqlitedb.insert_data('most_model',(datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'),most_common_model,),columns=('ds','most_common_model',))






if is_corr:
    df = corr_feature(df=df)

df1 = df.copy()  # 备份一下，后面特征筛选完之后加入ds y 列用
logger.info(f"开始训练模型...")
row,col = df.shape

now = datetime.datetime.now().strftime('%Y%m%d%H%M%S')




In [ ]:
model_results3 = model_losss(sqlitedb)


开始绘制Kpler数据--原油出口类指标的相关性直方图
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):


Kpler数据--原油出口下正相关的特征值有： []
Kpler数据--原油出口下负相关的特征值有： ['Libya', 'Malaysia']
正在绘制第1个特征Libya与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第2个特征Malaysia与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

...

d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第4个特征中国独立炼厂原油加工量-隆众与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第5个特征美国柴油产量占比与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating